In [1]:
from list_questions import load_questions
from extract_keywords import extract_keywords, extract_keywords2
db_name = 'omnidesk-ai-chatgpt-questions.sqlite'

In [2]:
from sentence_transformers import InputExample
import random

def get_user_question(q):
    keywords = extract_keywords2(q['query'])
    return ' '.join([q['question'].strip(), ' '.join(keywords)]).lower()
  
def get_system_question(q):
    return q['query'].lower()
  
def get_negative_system_question(q, all_questions):
    negative_q = random.choice(list(filter(lambda q2: q['query'] != q2['query'], all_questions)))
    return negative_q['query'].lower()

def input_example_generator():
    all_questions = list(load_questions(db_name))
    for q in all_questions:
        yield InputExample(texts=[get_user_question(q), get_system_question(q)], label=1.0)
        yield InputExample(texts=[get_user_question(q), get_negative_system_question(q, all_questions)], label=0.0)

In [3]:
from torch.utils.data import IterableDataset, DataLoader

additional_examples = [
  InputExample(texts=['добрый день', 'добрый день, здравствуйте'], label=1.0),
  InputExample(texts=['здравствуйте', 'добрый день, здравствуйте'], label=1.0),
  InputExample(texts=['привет', 'добрый день, здравствуйте'], label=1.0),
  InputExample(texts=['спасибо', 'спасибо, до свидания'], label=1.0),
  InputExample(texts=['до свидания', 'спасибо, до свидания'], label=1.0),
  InputExample(texts=['не понял', 'некорректный ответ, не понял'], label=1.0),
  InputExample(texts=['некорректный ответ', 'некорректный ответ, не понял'], label=1.0),
  InputExample(texts=['как убрать ошибку', 'как убрать ошибку'], label=1.0),
  InputExample(texts=['как устранить ошибку', 'как убрать ошибку'], label=1.0),
  InputExample(texts=['как решить проблему с ошибкой', 'как убрать ошибку'], label=1.0),
  InputExample(texts=['есть ли способ устранить ошибку', 'как убрать ошибку'], label=1.0),
  InputExample(texts=['каким образом можно избавиться от ошибки', 'как убрать ошибку'], label=1.0),
  InputExample(texts=['позови человека', 'позови человека сотрудника менеджера оператора'], label=1.0),
  InputExample(texts=['позови сотрудника', 'позови человека сотрудника менеджера оператора'], label=1.0),
  InputExample(texts=['позови менеджера', 'позови человека сотрудника менеджера оператора'], label=1.0),
  InputExample(texts=['позови оператора', 'позови человека сотрудника менеджера оператора'], label=1.0),
  InputExample(texts=['оператор', 'позови человека сотрудника менеджера оператора'], label=1.0),
  InputExample(texts=['человек', 'позови человека сотрудника менеджера оператора'], label=1.0),
  
  # special cases
  InputExample(texts=['можете подсказать, что делать с ошибкой', 'как убрать ошибку'], label=4.0),
  InputExample(texts=['что произойдет при удалении оплаты cloudpayments', 'cloudpayments перенос оплаты в платежных модулях на примере модуля cloudpayments что произойдет при удалении оплаты'], label=1.0),
  InputExample(texts=['превышен лимит количества контактов unisender', 'экспорт сегментов в unisender ошибка превышен лимит количества контактов для текущего превышен лимит количества контактов'], label=1.0),
  InputExample(texts=['не отображаются тарифы', 'не передаются тарифы'], label=0.0),
  
  # ???
  InputExample(texts=['почему количество пользователей отличается', 'почему clientid отличается'], label=0.0),
  InputExample(texts=['что означает галка \'доставка курьером\'', 'что означает галка доставка курьером'], label=1.0),
  
  InputExample(texts=['почта россии', 'яндекс доставка'], label=0.0),
  InputExample(texts=['почта россии', 'яндекс метрика'], label=0.0),
  InputExample(texts=['яндекс доставка', 'яндекс метрика'], label=0.0),
  InputExample(texts=['unisender', 'яндекс доставка'], label=0.0),
  InputExample(texts=['альфабанк', 'яндекс доставка'], label=0.0),
  InputExample(texts=['почта россии', 'яндекс аудитории'], label=0.0),
  InputExample(texts=['sipuni', 'cloudpayments'], label=0.0),
  InputExample(texts=['sipuni', 'facebook'], label=0.0),
  InputExample(texts=['robokassa', 'вконтакте'], label=0.0),
  InputExample(texts=['robokassa', 'digital pipeline'], label=0.0),
  InputExample(texts=['facebook', 'вконтакте'], label=0.0),
  InputExample(texts=['facebook', 'mailchimp'], label=0.0),
  InputExample(texts=['почта россии', 'cloudpayments'], label=0.0),
]

train_dataloader = DataLoader(list(input_example_generator()) + additional_examples, batch_size=16)

# Pretrain

In [4]:
from sentence_transformers import CrossEncoder
model = CrossEncoder('cross-encoder/mmarco-mMiniLMv2-L12-H384-v1')

2023-08-22 14:47:41.400087: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [5]:
from sentence_transformers import InputExample
pretrain_samples = [
  #InputExample(texts=['тест', 'тест'], label=1.0),
  InputExample(texts=['пока', 'до свидания'], label=1.0),
  InputExample(texts=['как настроить модуль', 'как настроить модуль'], label=1.0),
  InputExample(texts=['как настроить модуль яндекс доставка', 'как настроить модуль почта россии'], label=0.0),
  InputExample(texts=['как настроить модуль почта россии', 'как настроить модуль robokassa'], label=0.0),
  InputExample(texts=['как настроить модуль яндекс доставка', 'как настроить модуль robokassa'], label=0.0),
  # InputExample(texts=['ошибка сервиса доставки почта россии', 'ошибка сервиса почта россии'], label=1.0),
  InputExample(texts=['ошибка дата отгрузки, полученная от яндекс.доставки', 'ошибка даты отгрузки яндекс доставки'], label=1.0),
  InputExample(texts=['ошибка дата отгрузки, полученная от яндекс.доставки', 'яндекс доставка ошибка сервиса доставки при выборе терминала отгрузки'], label=0.0),
]

In [6]:
from torch.utils.data import DataLoader
pretrain_dataloader = DataLoader(pretrain_samples)

In [7]:
model.fit(pretrain_dataloader, epochs=4, optimizer_params={'lr': 1e-1, 'eps': 1e-6})

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Iteration:   0%|          | 0/7 [00:00<?, ?it/s]

Iteration:   0%|          | 0/7 [00:00<?, ?it/s]

Iteration:   0%|          | 0/7 [00:00<?, ?it/s]

Iteration:   0%|          | 0/7 [00:00<?, ?it/s]

In [8]:
model.predict([
  ('добрый день', 'здравствуйте'),
  ('добрый день', 'привет'),
  ('как исправить ошибку', 'как убрать ошибку'),
  ('какой сегодня прекрасный день', 'некорректный ответ не понял'),
  ('как настроить модуль яндекс доставка', 'как настроить модуль сдэк'),
])

array([  7.250268,   7.564313,  10.511606,  -5.297707, -10.485567],
      dtype=float32)

In [9]:
model.fit(train_dataloader, epochs=1, optimizer_params={'lr': 1e-3, 'eps': 1e-6})

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Iteration:   0%|          | 0/50 [00:00<?, ?it/s]

In [10]:
model.predict([
  ('добрый день', 'здравствуйте'),
  ('добрый день', 'привет'),
  ('как исправить ошибку', 'как убрать ошибку'),
  ('какой сегодня прекрасный день', 'некорректный ответ не понял'),
  ('как настроить модуль яндекс доставка', 'как настроить модуль сдэк'),
])

array([  6.8022833,   7.1733284,  10.234115 ,  -5.4563026, -10.522914 ],
      dtype=float32)

In [11]:
labels = [example.label for example in train_dataloader.dataset]
predicts = model.predict([example.texts for example in train_dataloader.dataset], show_progress_bar=True)

Batches:   0%|          | 0/25 [00:00<?, ?it/s]

In [12]:
import math

for label, predict, example in zip(labels, predicts, train_dataloader.dataset):
    label1 = 1.0 if math.copysign(1, predict) == 1.0 else 0.0
    if (label != label1):
        print(label, predict)
        print('===', example.texts[0])
        print('===', example.texts[1])

0.0 0.65314835
=== почему кол-во пользователей в сегменте аудиторий отличается от кол-ва пользователей в сегменте в retailcrm? яндекс аудитория retailcrm
=== экспорт сегментов в вконтакте минимальное число контактов в сегменте для загрузки в вконтакте какое минимальное число контактов нужно загрузить в вконтакте
1.0 -9.538332
=== какие два случая рассматриваются в статье? digital pipeline почта россия
=== digital pipline принцип работы типа синхронизации точное соответствие какие два случая рассматриваются в статье
1.0 -0.25401944
=== превышен лимит количества контактов почта россия mailchimp
=== экспорт сегментов в mailchimp ошибка превышен лимит количества контактов превышен лимит количества контактов
1.0 -6.570962
=== как добавить клиентский аккаунт? маркетинговый расход почта россия
=== маркетинговые расходы добавление аккаунта представителя как добавить клиентский аккаунт
0.0 3.0155332
=== как подключить модуль sipuni?
подключение модуля sipuni sipuni
=== почта россии работа с мар